# 5장. 자연어 처리 소개

<table class="tfo-notebook-buttons" align="left">
  <td>
    <a target="_blank" href="https://nbviewer.jupyter.org/github/rickiepark/aiml4coders/blob/main/ch05/05-intro-nlp.ipynb"><img src="https://jupyter.org/assets/share.png" width="61" />주피터 노트북 뷰어로 보기</a>
  </td>
  <td>
    <a target="_blank" href="https://colab.research.google.com/github/rickiepark/aiml4coders/blob/main/ch05/05-intro-nlp.ipynb"><img src="https://www.tensorflow.org/images/colab_logo_32px.png" />구글 코랩(Colab)에서 실행하기</a>
  </td>
</table>

In [1]:
# 노트북이 코랩에서 실행 중인지 체크합니다.
import sys
if 'google.colab' in sys.modules:
    !wget -q https://github.com/rickiepark/aiml4coders/raw/main/ch05/binary-emotion.csv
    !wget -q https://github.com/rickiepark/aiml4coders/raw/main/ch05/sarcasm.json

## 언어를 숫자로 인코딩하기

### 토큰화 시작하기

In [2]:
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras.preprocessing.text import Tokenizer

sentences = [
    'Today is a sunny day',
    'Today is a rainy day'
]

tokenizer = Tokenizer(num_words = 100)
tokenizer.fit_on_texts(sentences)
word_index = tokenizer.word_index
print(word_index)

{'today': 1, 'is': 2, 'a': 3, 'day': 4, 'sunny': 5, 'rainy': 6}


In [3]:
tokenizer.index_word

{1: 'today', 2: 'is', 3: 'a', 4: 'day', 5: 'sunny', 6: 'rainy'}

In [4]:
tokenizer.word_counts

OrderedDict([('today', 2),
             ('is', 2),
             ('a', 2),
             ('sunny', 1),
             ('day', 2),
             ('rainy', 1)])

In [5]:
sentences = [
    'Today is a sunny day',
    'Today is a rainy day',
    'Is it sunny today?'
]

In [6]:
tokenizer.fit_on_texts(sentences)
word_index = tokenizer.word_index
print(word_index)

{'today': 1, 'is': 2, 'a': 3, 'day': 4, 'sunny': 5, 'rainy': 6, 'it': 7}


### 문장을 시퀀스로 바꾸기

In [7]:
sequences = tokenizer.texts_to_sequences(sentences)

print(sequences)

[[1, 2, 3, 5, 4], [1, 2, 3, 6, 4], [2, 7, 5, 1]]


#### OOV 토큰 사용하기

In [8]:
test_data = [
    'Today is a snowy day',
    'Will it be rainy tomorrow?'
]

In [9]:
test_sequences = tokenizer.texts_to_sequences(test_data)
print(word_index)
print(test_sequences)

{'today': 1, 'is': 2, 'a': 3, 'day': 4, 'sunny': 5, 'rainy': 6, 'it': 7}
[[1, 2, 3, 4], [7, 6]]


In [10]:
tokenizer = Tokenizer(num_words = 100, oov_token="<OOV>")
tokenizer.fit_on_texts(sentences)
word_index = tokenizer.word_index

test_sequences = tokenizer.texts_to_sequences(test_data)
print(word_index)
print(test_sequences)

{'<OOV>': 1, 'today': 2, 'is': 3, 'a': 4, 'sunny': 5, 'day': 6, 'rainy': 7, 'it': 8}
[[2, 3, 4, 1, 6], [1, 8, 1, 7, 1]]


##### `TextVectorization` 층 사용하기

In [11]:
tv = keras.layers.TextVectorization(max_tokens=100)
tv.adapt(sentences)

In [12]:
tv.get_vocabulary()

['', '[UNK]', 'today', 'is', 'sunny', 'day', 'a', 'rainy', 'it']

In [13]:
test_seq = tv(test_data)
test_seq.numpy()

array([[2, 3, 6, 1, 5],
       [1, 8, 1, 7, 1]])

#### 패딩 이해하기

In [14]:
sentences = [
    'Today is a sunny day',
    'Today is a rainy day',
    'Is it sunny today?',
    'I really enjoyed walking in the snow today'
]

In [15]:
tokenizer.fit_on_texts(sentences)
sequences = tokenizer.texts_to_sequences(sentences)
print(sequences)

[[2, 3, 4, 5, 6], [2, 3, 4, 7, 6], [3, 8, 5, 2], [9, 10, 11, 12, 13, 14, 15, 2]]


In [16]:
from tensorflow.keras.preprocessing.sequence import pad_sequences

In [17]:
padded = pad_sequences(sequences)

print(padded)

[[ 0  0  0  2  3  4  5  6]
 [ 0  0  0  2  3  4  7  6]
 [ 0  0  0  0  3  8  5  2]
 [ 9 10 11 12 13 14 15  2]]


In [18]:
padded = pad_sequences(sequences, padding='post')

print(padded)

[[ 2  3  4  5  6  0  0  0]
 [ 2  3  4  7  6  0  0  0]
 [ 3  8  5  2  0  0  0  0]
 [ 9 10 11 12 13 14 15  2]]


In [19]:
padded = pad_sequences(sequences, padding='post', maxlen=6)

print(padded)

[[ 2  3  4  5  6  0]
 [ 2  3  4  7  6  0]
 [ 3  8  5  2  0  0]
 [11 12 13 14 15  2]]


In [20]:
padded = pad_sequences(sequences, padding='post', maxlen=6, truncating='post')
 
print(padded)

[[ 2  3  4  5  6  0]
 [ 2  3  4  7  6  0]
 [ 3  8  5  2  0  0]
 [ 9 10 11 12 13 14]]


## 실제 데이터 다루기

### 텐서플로 데이터셋에서 텍스트 가져오기

In [21]:
import tensorflow_datasets as tfds

imdb_sentences = []
train_data = tfds.as_numpy(tfds.load('imdb_reviews', split="train"))
for item in train_data:
    imdb_sentences.append(str(item['text']))

Dl Completed...: 0 url [00:00, ? url/s]

Dl Size...: 0 MiB [00:00, ? MiB/s]

Generating splits...:   0%|          | 0/3 [00:00<?, ? splits/s]

Generating train examples...:   0%|          | 0/25000 [00:00<?, ? examples/s]

Shuffling ~/tensorflow_datasets/imdb_reviews/plain_text/1.0.0.incompleteG8DL3V/imdb_reviews-train.tfrecord*...…

Generating test examples...:   0%|          | 0/25000 [00:00<?, ? examples/s]

Shuffling ~/tensorflow_datasets/imdb_reviews/plain_text/1.0.0.incompleteG8DL3V/imdb_reviews-test.tfrecord*...:…

Generating unsupervised examples...:   0%|          | 0/50000 [00:00<?, ? examples/s]

Shuffling ~/tensorflow_datasets/imdb_reviews/plain_text/1.0.0.incompleteG8DL3V/imdb_reviews-unsupervised.tfrec…

Dataset imdb_reviews downloaded and prepared to ~/tensorflow_datasets/imdb_reviews/plain_text/1.0.0. Subsequent calls will reuse this data.


In [22]:
tokenizer = tf.keras.preprocessing.text.Tokenizer(num_words=5000)
tokenizer.fit_on_texts(imdb_sentences)
sequences = tokenizer.texts_to_sequences(imdb_sentences)

In [23]:
# 출력이 길어 노트북에서 제외함
print(tokenizer.word_index)

{'the': 1, 'and': 2, 'a': 3, 'of': 4, 'to': 5, 'is': 6, 'br': 7, 'in': 8, 'it': 9, 'i': 10, 'this': 11, 'that': 12, 'was': 13, 'as': 14, 'for': 15, 'with': 16, 'movie': 17, 'but': 18, 'film': 19, "'s": 20, 'on': 21, 'you': 22, 'not': 23, 'are': 24, 'his': 25, 'he': 26, 'have': 27, 'be': 28, 'one': 29, 'all': 30, 'at': 31, 'by': 32, 'they': 33, 'an': 34, 'who': 35, 'so': 36, 'from': 37, 'like': 38, 'her': 39, "'t": 40, 'or': 41, 'just': 42, 'there': 43, 'about': 44, 'out': 45, "'": 46, 'has': 47, 'if': 48, 'some': 49, 'what': 50, 'good': 51, 'more': 52, 'very': 53, 'when': 54, 'she': 55, 'up': 56, 'can': 57, 'b': 58, 'time': 59, 'no': 60, 'even': 61, 'my': 62, 'would': 63, 'which': 64, 'story': 65, 'only': 66, 'really': 67, 'see': 68, 'their': 69, 'had': 70, 'were': 71, 'me': 72, 'well': 73, 'we': 74, 'than': 75, 'much': 76, 'been': 77, 'get': 78, 'bad': 79, 'will': 80, 'people': 81, 'do': 82, 'also': 83, 'other': 84, 'into': 85, 'because': 86, 'great': 87, 'first': 88, 'him': 89, 'how'

In [24]:
from bs4 import BeautifulSoup
import string

stopwords = ["a", "about", "above", "after", "again", "against", "all", "am", "an", "and", "any", "are", "as", "at",
             "be", "because", "been", "before", "being", "below", "between", "both", "but", "by", "could", "did", "do",
             "does", "doing", "down", "during", "each", "few", "for", "from", "further", "had", "has", "have", "having",
             "he", "hed", "hes", "her", "here", "heres", "hers", "herself", "him", "himself", "his", "how",
             "hows", "i", "id", "ill", "im", "ive", "if", "in", "into", "is", "it", "its", "itself",
             "lets", "me", "more", "most", "my", "myself", "nor", "of", "on", "once", "only", "or", "other", "ought",
             "our", "ours", "ourselves", "out", "over", "own", "same", "she", "shed", "shell", "shes", "should",
             "so", "some", "such", "than", "that", "thats", "the", "their", "theirs", "them", "themselves", "then",
             "there", "theres", "these", "they", "theyd", "theyll", "theyre", "theyve", "this", "those", "through",
             "to", "too", "under", "until", "up", "very", "was", "we", "wed", "well", "were", "weve", "were",
             "what", "whats", "when", "whens", "where", "wheres", "which", "while", "who", "whos", "whom", "why",
             "whys", "with", "would", "you", "youd", "youll", "youre", "youve", "your", "yours", "yourself",
             "yourselves"]

table = str.maketrans('', '', string.punctuation)

imdb_sentences = []
train_data = tfds.as_numpy(tfds.load('imdb_reviews', split="train"))
for item in train_data:
    sentence = str(item['text'].decode('UTF-8').lower())
    sentence = sentence.replace(",", " , ")
    sentence = sentence.replace(".", " . ")
    sentence = sentence.replace("-", " - ")
    sentence = sentence.replace("/", " / ")
    soup = BeautifulSoup(sentence)
    sentence = soup.get_text()
    words = sentence.split()
    filtered_sentence = ""
    for word in words:
        word = word.translate(table)
        if word not in stopwords:
            filtered_sentence = filtered_sentence + word + " "
    imdb_sentences.append(filtered_sentence)

tokenizer = tf.keras.preprocessing.text.Tokenizer(num_words=25000)
tokenizer.fit_on_texts(imdb_sentences)
sequences = tokenizer.texts_to_sequences(imdb_sentences)
# 출력이 길어 노트북에서 제외함
print(tokenizer.word_index)

{'movie': 1, 'film': 2, 'not': 3, 'one': 4, 'like': 5, 'just': 6, 'good': 7, 'no': 8, 'time': 9, 'even': 10, 'story': 11, 'really': 12, 'see': 13, 'can': 14, 'much': 15, 'bad': 16, 'get': 17, 'will': 18, 'also': 19, 'people': 20, 'great': 21, 'first': 22, 'dont': 23, 'made': 24, 'movies': 25, 'make': 26, 'way': 27, 'films': 28, 'characters': 29, 'think': 30, 'watch': 31, 'two': 32, 'character': 33, 'many': 34, 'seen': 35, 'life': 36, 'plot': 37, 'never': 38, 'acting': 39, 'little': 40, 'love': 41, 'best': 42, 'show': 43, 'know': 44, 'off': 45, 'ever': 46, 'better': 47, 'end': 48, 'still': 49, 'man': 50, 'say': 51, 'scene': 52, 'scenes': 53, 'go': 54, 'something': 55, 'back': 56, 'real': 57, 'watching': 58, 'years': 59, 'now': 60, 'doesnt': 61, 'though': 62, 'actors': 63, 'old': 64, 'thing': 65, 'didnt': 66, 'work': 67, 'new': 68, 'another': 69, 'nothing': 70, 'funny': 71, 'actually': 72, '10': 73, 'makes': 74, 'director': 75, 'look': 76, 'find': 77, 'going': 78, 'part': 79, 'every': 80

In [25]:
sentences = [
    'Today is a sunny day',
    'Today is a rainy day',
    'Is it sunny today?'
]
sequences = tokenizer.texts_to_sequences(sentences)
print(sequences)

[[516, 5229, 147], [516, 6489, 147], [5229, 516]]


In [26]:
reverse_word_index = dict(
    [(value, key) for (key, value) in tokenizer.word_index.items()])

decoded_review = ' '.join([reverse_word_index.get(i, '?') for i in sequences[0]])

print(decoded_review)

today sunny day


In [27]:
decoded_review = ' '.join([tokenizer.index_word.get(i, '?') for i in sequences[0]])

print(decoded_review)

today sunny day


#### IMDb 보조단어 데이터셋 사용하기

In [28]:
(train_data, test_data), info = tfds.load(
    'imdb_reviews/subwords8k', 
    split = (tfds.Split.TRAIN, tfds.Split.TEST),
    as_supervised=True,
    with_info=True
)

Dl Completed...: 0 url [00:00, ? url/s]

Dl Size...: 0 MiB [00:00, ? MiB/s]

Generating splits...:   0%|          | 0/3 [00:00<?, ? splits/s]

Generating train examples...:   0%|          | 0/25000 [00:00<?, ? examples/s]

Shuffling ~/tensorflow_datasets/imdb_reviews/subwords8k/1.0.0.incomplete44YXVM/imdb_reviews-train.tfrecord*...…

Generating test examples...:   0%|          | 0/25000 [00:00<?, ? examples/s]

Shuffling ~/tensorflow_datasets/imdb_reviews/subwords8k/1.0.0.incomplete44YXVM/imdb_reviews-test.tfrecord*...:…

Generating unsupervised examples...:   0%|          | 0/50000 [00:00<?, ? examples/s]

Shuffling ~/tensorflow_datasets/imdb_reviews/subwords8k/1.0.0.incomplete44YXVM/imdb_reviews-unsupervised.tfrec…

Dataset imdb_reviews downloaded and prepared to ~/tensorflow_datasets/imdb_reviews/subwords8k/1.0.0. Subsequent calls will reuse this data.


In [29]:
encoder = info.features['text'].encoder
print ('어휘 사전 크기: {}'.format(encoder.vocab_size))

어휘 사전 크기: 8185


In [30]:
# 출력이 길어 노트북에서 제외함
print(encoder.subwords)

['the_', ', ', '. ', 'a_', 'and_', 'of_', 'to_', 's_', 'is_', 'br', 'in_', 'I_', 'that_', 'this_', 'it_', ' /><', ' />', 'was_', 'The_', 'as_', 't_', 'with_', 'for_', '.<', 'on_', 'but_', 'movie_', ' (', 'are_', 'his_', 'have_', 'film_', 'not_', 'ing_', 'be_', 'ed_', 'you_', ' "', 'it', 'd_', 'an_', 'he_', 'by_', 'at_', 'one_', 'who_', 'y_', 'from_', 'e_', 'or_', 'all_', 'like_', 'they_', '" ', 'so_', 'just_', 'has_', ') ', 'her_', 'about_', 'out_', 'This_', 'some_', 'ly_', 'movie', 'film', 'very_', 'more_', 'It_', 'would_', 'what_', 'when_', 'which_', 'good_', 'if_', 'up_', 'only_', 'even_', 'their_', 'had_', 'really_', 'my_', 'can_', 'no_', 'were_', 'see_', 'she_', '? ', 'than_', '! ', 'there_', 'get_', 'been_', 'into_', ' - ', 'will_', 'much_', 'story_', 'because_', 'ing', 'time_', 'n_', 'we_', 'ed', 'me_', ': ', 'most_', 'other_', 'don', 'do_', 'm_', 'es_', 'how_', 'also_', 'make_', 'its_', 'could_', 'first_', 'any_', "' ", 'people_', 'great_', 've_', 'ly', 'er_', 'made_', 'r_', 'B

In [31]:
sample_string = 'Today is a sunny day'

encoded_string = encoder.encode(sample_string)
print ('인코딩된 문자열: {}'.format(encoded_string))

인코딩된 문자열: [6427, 4869, 9, 4, 2365, 1361, 606]


In [32]:
print(encoder.subwords[6426])

Tod


In [33]:
encoded_string = encoder.encode(sample_string)

original_string = encoder.decode(encoded_string)
test_string = encoder.decode([6427, 4869, 9, 4, 2365, 1361, 606])

### CSV 파일에서 텍스트 읽기

In [34]:
import csv
sentences=[]
labels=[]
with open('binary-emotion.csv', encoding='UTF-8') as csvfile:
    reader = csv.reader(csvfile, delimiter=",")
    for row in reader:
        labels.append(int(row[0]))
        sentence = row[1].lower()
        sentence = sentence.replace(",", " , ")
        sentence = sentence.replace(".", " . ")
        sentence = sentence.replace("-", " - ")
        sentence = sentence.replace("/", " / ")
        soup = BeautifulSoup(sentence)
        sentence = soup.get_text()
        words = sentence.split()
        filtered_sentence = ""
        for word in words:
            word = word.translate(table)
            if word not in stopwords:
                filtered_sentence = filtered_sentence + word + " "
        sentences.append(filtered_sentence)

#### 훈련 세트와 테스트 세트 만들기

In [35]:
training_size = 28000
training_sentences = sentences[0:training_size]
testing_sentences = sentences[training_size:]
training_labels = labels[0:training_size]
testing_labels = labels[training_size:]

In [36]:
vocab_size = 20000
max_length = 10
trunc_type='post'
padding_type='post'
oov_tok = "<OOV>"
tokenizer = Tokenizer(num_words=vocab_size, oov_token=oov_tok)
tokenizer.fit_on_texts(training_sentences)
word_index = tokenizer.word_index
training_sequences = tokenizer.texts_to_sequences(training_sentences)
training_padded = pad_sequences(training_sequences, maxlen=max_length, 
                                padding=padding_type, truncating=trunc_type)

In [37]:
print(training_sequences[0])
print(training_padded[0])

[18, 3257, 47, 4770, 613, 508, 951, 423]
[  18 3257   47 4770  613  508  951  423    0    0]


In [38]:
# 출력이 길어 노트북에서 제외함
print(tokenizer.word_index)

{'<OOV>': 1, 'just': 2, 'not': 3, 'now': 4, 'day': 5, 'get': 6, 'no': 7, 'good': 8, 'like': 9, 'go': 10, 'dont': 11, 'work': 12, 'today': 13, 'got': 14, 'cant': 15, 'going': 16, 'one': 17, 'know': 18, 'back': 19, 'time': 20, 'love': 21, 'really': 22, 'will': 23, 'lol': 24, 'com': 25, 'u': 26, 'see': 27, 'want': 28, 'can': 29, 'home': 30, 'new': 31, 'think': 32, '2': 33, 'still': 34, 'oh': 35, 'miss': 36, 'much': 37, 'off': 38, 'need': 39, 'night': 40, 'last': 41, 'feel': 42, 'sad': 43, 'wish': 44, 'hope': 45, 'sorry': 46, 'bad': 47, 'didnt': 48, 'great': 49, 'morning': 50, 'thanks': 51, 'haha': 52, 'tomorrow': 53, 'twitter': 54, 'happy': 55, '3': 56, 'right': 57, 'tonight': 58, 'though': 59, 'gonna': 60, 'week': 61, 'fun': 62, 'make': 63, 'better': 64, 'weekend': 65, 'getting': 66, 'way': 67, 'nice': 68, 'come': 69, 'school': 70, 'sleep': 71, 'yeah': 72, 'hate': 73, 'people': 74, 'next': 75, 'days': 76, 'wont': 77, 'even': 78, 'never': 79, 'working': 80, 'say': 81, 'long': 82, 'wait': 

### JSON 파일에서  텍스트 읽기

#### JSON 파일 읽기

In [39]:
import json
with open("sarcasm.json", 'r') as f:
    datastore = json.load(f)
    for item in datastore:
        sentence = item['headline'].lower()
        label= item['is_sarcastic']
        link = item['article_link']

In [40]:
with open("sarcasm.json", 'r') as f:
    datastore = json.load(f)

sentences = [] 
labels = []
urls = []
for item in datastore:
    sentence = item['headline'].lower()
    sentence = sentence.replace(",", " , ")
    sentence = sentence.replace(".", " . ")
    sentence = sentence.replace("-", " - ")
    sentence = sentence.replace("/", " / ")
    soup = BeautifulSoup(sentence)
    sentence = soup.get_text()
    words = sentence.split()
    filtered_sentence = ""
    for word in words:
        word = word.translate(table)
        if word not in stopwords:
            filtered_sentence = filtered_sentence + word + " "
    sentences.append(filtered_sentence)
    labels.append(item['is_sarcastic'])
    urls.append(item['article_link'])

In [41]:
training_size = 23000
training_sentences = sentences[0:training_size]
testing_sentences = sentences[training_size:]
training_labels = labels[0:training_size]
testing_labels = labels[training_size:]

In [42]:
vocab_size = 20000
max_length = 10
trunc_type='post'
padding_type='post'
oov_tok = "<OOV>"

tokenizer = Tokenizer(num_words=vocab_size, oov_token=oov_tok)
tokenizer.fit_on_texts(training_sentences)

word_index = tokenizer.word_index

training_sequences = tokenizer.texts_to_sequences(training_sentences)
training_padded = pad_sequences(training_sequences, maxlen=max_length, 
                                padding=padding_type, truncating=trunc_type)
# 출력이 길어 노트북에서 제외함
print(word_index)

{'<OOV>': 1, 'new': 2, 'trump': 3, 'man': 4, 'not': 5, 'just': 6, 'will': 7, 'one': 8, 'year': 9, 'report': 10, 'area': 11, 'donald': 12, 'day': 13, 'u': 14, 's': 15, 'can': 16, 'says': 17, 'woman': 18, 'first': 19, 'time': 20, 'like': 21, 'no': 22, 'get': 23, 'old': 24, 'trumps': 25, 'off': 26, 'now': 27, 'life': 28, 'obama': 29, 'people': 30, 'house': 31, 'women': 32, 'white': 33, 'back': 34, 'still': 35, 'make': 36, 'clinton': 37, '5': 38, 'world': 39, 'americans': 40, 'years': 41, 'way': 42, 'family': 43, 'black': 44, 'study': 45, 'gop': 46, 'best': 47, 'bill': 48, 'american': 49, 'school': 50, 'police': 51, 'watch': 52, '3': 53, 'show': 54, 'really': 55, 'president': 56, 'home': 57, 'last': 58, 'video': 59, 'finds': 60, 'death': 61, 'cant': 62, 'know': 63, '10': 64, 'things': 65, 'good': 66, 'going': 67, 'state': 68, 'hillary': 69, 'love': 70, 'nation': 71, 'may': 72, '2': 73, 'health': 74, 'say': 75, 'parents': 76, 'big': 77, 'every': 78, 'right': 79, 'work': 80, '000': 81, 'need